<em><sub>This page is available as an executable or viewable <strong>Jupyter Notebook</strong>:</sub></em>
<br/><br/>
<a href="https://mybinder.org/v2/gh/JetBrains/lets-plot/v2.0.3demos1?filepath=docs%2Fexamples%2Fjupyter-notebooks%2Fgeocoding_examples.ipynb"
   target="_parent">
   <img align="left"
        src="https://mybinder.org/badge_logo.svg">
</a>
<a href="https://nbviewer.jupyter.org/github/JetBrains/lets-plot/blob/master/docs/examples/jupyter-notebooks/geocoding_examples.ipynb"
   target="_parent">
   <img align="right"
        src="https://raw.githubusercontent.com/jupyter/design/master/logos/Badges/nbviewer_badge.png"
        width="109" height="20">
</a>
<br/>
<br/>


In [1]:
from lets_plot import *
LetsPlot.setup_html()

In [2]:
from lets_plot.geo_data import *

The geodata is provided by © OpenStreetMap contributors and is made available here under the Open Database License (ODbL).


### Sweden and Finland

#### Create countries geocoder.

In [3]:
country_gcoder = geocode_countries(['Finland', 'Sweden'])
country_gcoder.get_geocodes()

id  country found name
0  108449  Finland      Suomi
1  105645   Sweden    Sverige

In [4]:
map_options = (theme(axis_line="blank", axis_text="blank", axis_title="blank", axis_ticks="blank") +
               coord_map())

#### Plot  boundary polygons.

In [5]:
(ggplot() + 
 geom_polygon(aes(fill='found name'), 
              data=country_gcoder.get_boundaries(),
              tooltips=layer_tooltips().line("^fill"),
              color="white") +
 map_options + 
 scale_fill_hue(name="Country"))


#### Plot ploygons on interactive base-map.

Note: *nbviewer* won't load base-map tiles due to its CSP.

In [6]:
(ggplot() + geom_livemap() + 
 geom_polygon(aes(fill='found name'), 
              data=country_gcoder.get_boundaries(),
              tooltips=layer_tooltips().line("^fill"),
              color="white") +
 scale_fill_hue(name="Country"))


### The World

#### Create countries geocoder.

In [7]:
world_gcoder = geocode_countries()
world_gcoder.get_geocodes().head(3)

id                 country              found name
0  99431                  Polska                  Polska
1  99797  ព្រះរាជាណាចក្រ​កម្ពុជា  ព្រះរាជាណាចក្រ​កម្ពុជា
2  99807                ປະເທດລາວ                ປະເທດລາວ

#### World choropleth.

In [8]:
(ggplot() + 
 geom_polygon(aes(fill='found name'), 
              data=world_gcoder.get_boundaries(), 
              color="white", 
              tooltips=layer_tooltips().line("^fill"),
              show_legend=False) +
 map_options +
 scale_fill_brewer(name="Country", palette="Dark2") + 
 ggsize(900, 600))


### New York State and New York City.

In [9]:
(ggplot() + 
 geom_polygon(map=geocode_states("New York"), fill="#01327A") +
 geom_polygon(map=geocode_cities("New York"), fill="#F2C010") +
 map_options)

### The US states.

#### Create state geocoder for the US [48 contiguous states](https://en.wikipedia.org/wiki/Contiguous_United_States) (aka CONUS).

In [10]:
conus_gcoder = geocode_states('us-48').inc_res()

#### The US choropleth.

In [11]:
conus_plot = (ggplot() +
              geom_polygon(aes(fill='found name'), 
                           data=conus_gcoder.get_boundaries(), 
                           show_legend=False, 
                           color="white",
                           tooltips=layer_tooltips().line("^fill")) +
              map_options +
              scale_fill_brewer(name="State", palette="Dark2") + 
              ggsize(900, 500))
conus_plot

#### Add the states of Alaska and Hawaii.

In [12]:
alaska_plot = (ggplot() + geom_map(map=geocode_states('alaska'), 
                                   fill="light-blue", 
                                   color="#172048",
                                   tooltips=layer_tooltips().line("Alaska")) +
               xlim(-180, -130) + map_options)
hawaii_plot = (ggplot() + geom_map(map=geocode_states('hawaii'), 
                                   fill="#00A954", 
                                   color="#D91023",
                                   tooltips=layer_tooltips().line("Hawaii")) +
               xlim(-162, -154) + ylim(18, 23) +
               map_options)

bunch = GGBunch()
bunch.add_plot(conus_plot, 0, 0, 800, 400)
bunch.add_plot(alaska_plot, 0, 300, 200, 200)
bunch.add_plot(hawaii_plot, 200, 370, 200, 125)
bunch

### Resolving ambiguity.

#### There are many cities named "Warwick".

In [13]:
# Create a Warwick city geocoder.
world_warwicks = geocode_cities('warwick').allow_ambiguous()

# Plot Warwicks.
(ggplot() + geom_map(map=geocode_countries())
    + geom_point(map=world_warwicks, size=3, color="red")
    + coord_map(xlim=[-130, 20]))


#### Find one Warwick which is closest to Boston, US.

Note that the name "Boston" is not unique either. Therefore we will need two geocoders: one for Boston, US, and the other for the town of Warwick near Boston.

In [14]:
boston_us = geocode_cities('boston').countries('US')
warwick_near_boston = world_warwicks.where('warwick', closest_to=boston_us)

# Let's also geocode Massachusetts counties. 
counties_ma = geocode_counties().scope("Massachusetts")

In [15]:
(ggplot() + geom_map(map=counties_ma)
    + geom_point(map=warwick_near_boston, size=7, color="red") \
    + geom_polygon(map=boston_us))


#### Filter Warwicks using Shaply `box`.

In [16]:
from shapely.geometry import box
warwicks_in_box = (world_warwicks
    .where('warwick', scope=box(-72, 41.5, -71, 42)))


In [17]:
(ggplot() + geom_map(map=counties_ma)
    + geom_rect(xmin=-72, ymin=41.5, xmax=-71, ymax=42, alpha=0, color="magenta", linetype="dashed")
    + geom_point(map=warwicks_in_box, size=7, color="red")
    + geom_polygon(map=boston_us))


#### Explore the details on an interactive map.

Note: nbviewer won't load base-map tiles due to its CSP.

In [18]:
(ggplot() + geom_livemap()
    + geom_rect(xmin=-72, ymin=41.5, xmax=-71, ymax=42, alpha=0, color="magenta", linetype="dashed")
    + geom_point(map=warwicks_in_box, size=7, color="red")
    + geom_polygon(map=boston_us))
